# 캘리포니아 집 값 예측(회귀)

## 데이터 불러오기

In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from plotly.subplots import make_subplots

In [3]:
import optuna
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.linear_model import LinearRegression, Ridge, Lasso, ElasticNet
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor
from sklearn.metrics import r2_score
from sklearn.pipeline import Pipeline
from xgboost import XGBRegressor

In [4]:
df = pd.read_csv("../data/housing.csv")

In [5]:
df.shape

(20640, 10)

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20640 entries, 0 to 20639
Data columns (total 10 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   longitude           20640 non-null  float64
 1   latitude            20640 non-null  float64
 2   housing_median_age  20640 non-null  float64
 3   total_rooms         20640 non-null  float64
 4   total_bedrooms      20433 non-null  float64
 5   population          20640 non-null  float64
 6   households          20640 non-null  float64
 7   median_income       20640 non-null  float64
 8   median_house_value  20640 non-null  float64
 9   ocean_proximity     20640 non-null  object 
dtypes: float64(9), object(1)
memory usage: 1.6+ MB


In [7]:
df.describe()

longitude      latitude  housing_median_age   total_rooms   
count  20640.000000  20640.000000        20640.000000  20640.000000  \
mean    -119.569704     35.631861           28.639486   2635.763081   
std        2.003532      2.135952           12.585558   2181.615252   
min     -124.350000     32.540000            1.000000      2.000000   
25%     -121.800000     33.930000           18.000000   1447.750000   
50%     -118.490000     34.260000           29.000000   2127.000000   
75%     -118.010000     37.710000           37.000000   3148.000000   
max     -114.310000     41.950000           52.000000  39320.000000   

       total_bedrooms    population    households  median_income   
count    20433.000000  20640.000000  20640.000000   20640.000000  \
mean       537.870553   1425.476744    499.539680       3.870671   
std        421.385070   1132.462122    382.329753       1.899822   
min          1.000000      3.000000      1.000000       0.499900   
25%        296.000000    787.000000    280.000000       2.563400   
50%        435.000000   1166.000000    409.000000       3.534800   
75%        647.000000   1725.000000    605.000000       4.743250   
max       6445.000000  35682.000000   6082.000000      15.000100   

       median_house_value  
count        20640.000000  
mean        206855.816909  
std         115395.615874  
min          14999.000000  
25%         119600.000000  
50%         179700.000000  
75%         264725.000000  
max         500001.000000

In [8]:
df.isna().sum()

longitude               0
latitude                0
housing_median_age      0
total_rooms             0
total_bedrooms        207
population              0
households              0
median_income           0
median_house_value      0
ocean_proximity         0
dtype: int64

## 데이터 확인

In [9]:
fig = make_subplots(rows=3, cols=3, subplot_titles=("<i>longitude",
                                                    "<i>latitude",
                                                    "<i>housing_median_age",
                                                    "<i>total_rooms",
                                                    "<i>total_bedrooms",
                                                    "<i>population",
                                                    "<i>households",
                                                    "<i>median_income",
                                                    "<i>median_house_value"))
fig.add_trace(go.Histogram(x=df["longitude"], name="longitude"), row=1, col=1)
fig.add_trace(go.Histogram(x=df["latitude"], name="latitude"), row=1, col=2)
fig.add_trace(go.Histogram(x=df["housing_median_age"], name="housing_median_age"), row=1, col=3)
fig.add_trace(go.Histogram(x=df["total_rooms"], name="total_rooms"), row=2, col=1)
fig.add_trace(go.Histogram(x=df["total_bedrooms"], name="total_bedrooms"), row=2, col=2)
fig.add_trace(go.Histogram(x=df["population"], name="population"), row=2, col=3)
fig.add_trace(go.Histogram(x=df["households"], name="households"), row=3, col=1)
fig.add_trace(go.Histogram(x=df["median_income"], name="median_income"), row=3, col=2)
fig.add_trace(go.Histogram(x=df["median_house_value"], name="median_house_value"), row=3,col=3)
fig.update_layout(template="plotly_dark", title_text="<b>Distributions", title_x=0.5)

In [10]:
scl = [[0,"rgb(5, 10, 172)"],[0.35,"rgb(40, 60, 190)"],[0.5,"rgb(70, 100, 245)"],
       [0.6,"rgb(90, 120, 245)"],[0.7,"rgb(106, 137, 247)"],[1,"rgb(220, 220, 220)"]]
fig = px.box(df, x="ocean_proximity", y="median_house_value", template="plotly_dark", title="<b>Boxplots", color="ocean_proximity")
fig.update_layout(title_x=0.5)

In [11]:
fig=px.imshow(df.drop("ocean_proximity",axis=1).corr(),text_auto=True, template="plotly_dark", color_continuous_scale=px.colors.sequential.Blues, aspect="auto",title="<b>Correlation matrix")
fig.update_layout(title_x=0.5)

In [12]:
fig = px.scatter(df, x="median_income", y="median_house_value", trendline="ols", color_discrete_sequence=["steelbl"],
                 template="plotly_dark", title="<b>Target variable dependency on median_income", 
                 color="median_house_value", color_continuous_scale=px.colors.sequential.Blues)
fig.update_layout(title_x=0.5)

In [13]:
fig = px.bar(df.groupby("ocean_proximity", as_index=False).size().sort_values(by="size", ascending=False), x="ocean_proximity", y="size",
             color_discrete_sequence=["steelblue"], template="plotly_dark", title="<b> Number of different ocean_proximity values")
fig.update_layout(title_x=0.5)

In [14]:
fig = px.scatter_mapbox(df, lat="latitude", lon="longitude", size="median_house_value", size_max=10,
                        zoom=4.4, center=dict(lat=df["latitude"].mean() + 1, lon=df["longitude"].mean() - 1.5),
                        mapbox_style="stamen-terrain", template="plotly_dark", title="Dependence of the target variable on longitude, latitude", 
color="median_house_value")
fig.update_layout(title_x=0.5, height=600)

## 데이터 전처리

In [15]:
class DataPreprocessing:

    quantitative = ["longitude", "latitude", "housing_median_age", 
                    "total_rooms", "total_bedrooms", "population",
                    "households", "median_income"]

    ssc = StandardScaler()
    
    def __init__(self):
        self.q_25 = None
        self.q_75 = None
        self.means = None
        self.medians = None
    
    def fit(self, X, y=None):
        self.q_25 = X[DataPreprocessing.quantitative].quantile(q=0.25)
        self.medians = X[DataPreprocessing.quantitative].quantile(q=0.5)        
        self.q_75 = X[DataPreprocessing.quantitative].quantile(q=0.75)
        self.means = X[DataPreprocessing.quantitative].mean()

    def transform(self, X, y=None):
        for column in X[DataPreprocessing.quantitative].columns:
            q_3 = self.q_75[column]
            q_1 = self.q_25[column]
            iqr = q_3 - q_1
            upper_bound = q_3 + 1.5 * iqr
            lower_bound = q_1 - 1.5 * iqr
            X.loc[X[column] > upper_bound, column] = q_3
            X.loc[X[column] < lower_bound, column] = q_1
            
        for column in X[DataPreprocessing.quantitative].columns:
            X[column].fillna(self.means[column], inplace=True)
       
        # 새로운 컬럼을 추가     
        X["population_per_room"] = X["population"] / X["total_rooms"]        
        X["bedroom_share"] = X["total_bedrooms"] / X["total_rooms"] * 100    
        X["diag_coord"] = X["longitude"] + X["latitude"]    

        # one-hot encoding
        dummy = pd.get_dummies(X["ocean_proximity"])  
        X["_1H OCEAN"] = dummy["<1H OCEAN"]
        X["INLAND"] = dummy["INLAND"]
        X["ISLAND"] = dummy["ISLAND"] 
        X["NEAR BAY"] = dummy["NEAR BAY"]
        X["NEAR OCEAN"] = dummy["NEAR OCEAN"]
        X.drop(["ocean_proximity"],axis=1, inplace=True)
        
        X["age_cat"] = 0
        X.loc[X["housing_median_age"] <= 5, "age_cat"] = 1  
        X.loc[(X["housing_median_age"] > 5) & (X["housing_median_age"] <= 10), "age_cat"] = 2
        X.loc[(X["housing_median_age"] > 10) & (X["housing_median_age"] <= 25), "age_cat"] = 3
        X.loc[X["housing_median_age"] > 25, "age_cat"] = 4

    def scaling(X, data_type, y=None):
        if data_type.lower() == "train":
            return pd.DataFrame(DataPreprocessing.ssc.fit_transform(X), columns=X.columns, index=X.index)
        if data_type.lower() == "test":
            return pd.DataFrame(DataPreprocessing.ssc.transform(X), columns=X.columns, index=X.index)

## 데이터 분리(머신러닝을 위해서)

In [16]:
X = df[["longitude", "latitude", "housing_median_age", "total_rooms",
        "total_bedrooms", "population", "households", "median_income", 
        "ocean_proximity"]]
y = df["median_house_value"]
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42, shuffle=True, test_size=0.3)

In [17]:
preprocessing = DataPreprocessing()
preprocessing.fit(X)
preprocessing.transform(X_train)
preprocessing.transform(X_test)

In [18]:
X_train_scale = DataPreprocessing.scaling(X_train, "train")
X_test_scale = DataPreprocessing.scaling(X_test, "test")

## 데이터 학습 및 검증

In [20]:
rf = RandomForestRegressor()
rf.fit(X_train, y_train)
fig = go.Figure(go.Bar(x=rf.feature_importances_, y=X_train.columns, 
                       orientation="h", marker_color="steelblue"))
fig.update_layout(template="plotly_dark", title="<b>Estimating feature importance through the Random Forest model", 
                  title_x=0.5, xaxis_title="Feature importance", yaxis_title="Feature")
fig.show()

In [20]:
df_models = pd.DataFrame(data=None, columns=["Algorithm", "r2_train", "r2_test"])

def make_model(X_train, X_test, y_train, y_test, model, model_name):
    model.fit(X_train, y_train)
    y_pred_train = model.predict(X_train)
    y_pred_test = model.predict(X_test)
    r2_train = r2_score(y_train, y_pred_train)
    r2_test = r2_score(y_test, y_pred_test)
    df_models.loc[len(df_models.index)] = [model_name, r2_train, r2_test]

In [21]:
# 선형모델
make_model(X_train_scale, X_test_scale, y_train, y_test, LinearRegression(), "LinearRegression")
make_model(X_train_scale, X_test_scale, y_train, y_test, Ridge(), "Ridge")
make_model(X_train_scale, X_test_scale, y_train, y_test, Lasso(), "Lasso")
make_model(X_train_scale, X_test_scale, y_train, y_test, ElasticNet(), "ElasticNet")
# 랜덤 포레스트
make_model(X_train, X_test, y_train, y_test, GradientBoostingRegressor(), "GradientBoosting")
make_model(X_train, X_test, y_train, y_test, RandomForestRegressor(), "RandomForest")
make_model(X_train, X_test, y_train, y_test, XGBRegressor(), "XGBoost")

In [22]:
fig = go.Figure(data=[
    go.Bar(name="r2_train", x=df_models.Algorithm, y=df_models.r2_train),
    go.Bar(name="r2_test", x=df_models.Algorithm, y=df_models.r2_test)
])
fig.update_layout(template="plotly_dark", title="R2 for train and test", title_x=0.5)

## Auto Turning

In [38]:
X_trainval, X_valid, y_trainval, y_valid = train_test_split(X_train, y_train, shuffle=True,  random_state=42)

In [46]:
def objective(trial):
    param = {
        # "tree_method":"gpu_hist",
        # "sampling_method": "gradient_based",
        "random_state": 42,
        "lambda": trial.suggest_float("lambda", 7.0, 17.0),
        "alpha": trial.suggest_float("alpha", 7.0, 17.0),
        "eta": trial.suggest_categorical("eta", [0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]),
        "gamma": trial.suggest_categorical("gamma", [18, 19, 20, 21, 22, 23, 24, 25]),
        "learning_rate": trial.suggest_categorical("learning_rate", [0.008,0.01,0.012,0.014,0.016,0.018, 0.02]),
        "colsample_bytree": trial.suggest_categorical("colsample_bytree", [0.3,0.4,0.5,0.6,0.7,0.8,0.9, 1.0]),
        "colsample_bynode": trial.suggest_categorical("colsample_bynode", [0.3,0.4,0.5,0.6,0.7,0.8,0.9, 1.0]),
        "n_estimators": trial.suggest_int("n_estimators", 400, 1000),
        "min_child_weight": trial.suggest_int("min_child_weight", 8, 600),  
        "max_depth": trial.suggest_categorical("max_depth", [3, 4, 5, 6, 7]),  
        "subsample": trial.suggest_categorical("subsample", [0.5,0.6,0.7,0.8,1.0]),
        "early_stopping_rounds": 10,
    }
    model = XGBRegressor(**param)
    model.fit(X_trainval, y_trainval, eval_set=[(X_valid, y_valid)], verbose=False)
    predict = model.predict(X_valid)    
    r_2 = r2_score(predict, y_valid)    
    return r_2

In [47]:
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=5,  timeout=600)
# study.optimize(objective, n_trials=50,  timeout=600)

[I 2023-04-11 22:07:46,889] A new study created in memory with name: no-name-b7f41be5-2a2a-4827-a2ce-60d32246efb4
[I 2023-04-11 22:07:48,930] Trial 0 finished with value: 0.6970080735556032 and parameters: {'lambda': 10.49247956707598, 'alpha': 16.89474855747125, 'eta': 1.0, 'gamma': 25, 'learning_rate': 0.01, 'colsample_bytree': 0.5, 'colsample_bynode': 1.0, 'n_estimators': 797, 'min_child_weight': 453, 'max_depth': 7, 'subsample': 0.8}. Best is trial 0 with value: 0.6970080735556032.
[I 2023-04-11 22:07:50,594] Trial 1 finished with value: 0.6699423976790755 and parameters: {'lambda': 10.905652580855799, 'alpha': 15.825504925635121, 'eta': 0.4, 'gamma': 22, 'learning_rate': 0.008, 'colsample_bytree': 1.0, 'colsample_bynode': 0.3, 'n_estimators': 692, 'min_child_weight': 261, 'max_depth': 6, 'subsample': 0.7}. Best is trial 0 with value: 0.6970080735556032.
[I 2023-04-11 22:07:52,193] Trial 2 finished with value: 0.6747418763832296 and parameters: {'lambda': 14.618749201767315, 'alpha

In [48]:
print(f"Number of finished trials: {len(study.trials)}")
print("Best trial:")
trial = study.best_trial
print(f"\t\tValue: {trial.value}")
print(f"\t\tParams: ")
for key, value in trial.params.items():
    print(f"\t\t\t\t{key}: {value}")

Number of finished trials: 50
Best trial:
		Value: 0.8071611273061421
		Params: 
				lambda: 10.804312615280793
				alpha: 12.956754604756792
				eta: 0.4
				gamma: 20
				learning_rate: 0.02
				colsample_bytree: 0.9
				colsample_bynode: 0.7
				n_estimators: 885
				min_child_weight: 12
				max_depth: 7
				subsample: 1.0


In [49]:
fig = optuna.visualization.plot_slice(study)
fig.update_layout(template="plotly_dark", title="<b>Slice Plot", title_x=0.2)

In [50]:
fig = optuna.visualization.plot_param_importances(study)
fig.update_layout(template="plotly_dark", title="<b>Hyperparameter Importances", title_x=0.5)

In [51]:
best_model = XGBRegressor(**study.best_params)
best_model.fit(X_train, y_train)

XGBRegressor(alpha=12.956754604756792, base_score=None, booster=None,
             callbacks=None, colsample_bylevel=None, colsample_bynode=0.7,
             colsample_bytree=0.9, early_stopping_rounds=None,
             enable_categorical=False, eta=0.4, eval_metric=None,
             feature_types=None, gamma=20, gpu_id=None, grow_policy=None,
             importance_type=None, interaction_constraints=None,
             lambda=10.804312615280793, learning_rate=0.02, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=7, max_leaves=None,
             min_child_weight=12, missing=nan, monotone_constraints=None,
             n_estimators=885, n_jobs=None, ...)

In [52]:
print(f"Best model result in Test: {r2_score(y_test, best_model.predict(X_test))}")
print(f"Best model result in Train: {r2_score(y_train, best_model.predict(X_train))}")

Best model result in Test: 0.8542024407011011
Best model result in Train: 0.917954984460892


In [ ]:
#gradient_based
#Best model result in Test: 0.8406946716830559
#Best model result in Train: 0.8847647493578993

#auto
#Best model result in Test: 0.8542024407011011
#Best model result in Train: 0.917954984460892